In [1]:
from tensorflow.keras.layers import Dense
import matplotlib.pyplot as plt
from pandas import set_option
import pandas as pd
from tensorflow.keras.models import Sequential
import tensorflow.keras.utils
from tensorflow.keras.utils import plot_model
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input
from tensorflow.keras.layers import Dense, Dropout, Activation, Flatten, LSTM, BatchNormalization
import numpy as np 
from sklearn.metrics import confusion_matrix, classification_report
import seaborn as sn 
import tensorflow.keras
from tensorflow.keras.optimizers import SGD
from tensorflow.keras.models import model_from_json
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout
from tensorflow.keras.layers import Embedding
from tensorflow.keras.layers import Conv1D, GlobalAveragePooling1D, MaxPooling1D
from tensorflow.keras import regularizers

from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
from sklearn.preprocessing import LabelEncoder
from sklearn.pipeline import Pipeline
#from tensorflow.keras.utils import np_utils
from tensorflow.keras.wrappers.scikit_learn import KerasClassifier
from sklearn.model_selection import GridSearchCV
from tensorflow.keras.optimizers import SGD
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Dense, Flatten, Conv1D

from tensorflow.keras.layers import Dropout
#from tensorflow.keras.constraints import maxnorm
from sklearn import preprocessing
from sklearn import decomposition
from sklearn.model_selection import train_test_split

from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from sklearn.metrics import recall_score
from sklearn.metrics import precision_score
from sklearn.metrics import classification_report

import tensorflow as tf
import time as tm
import datetime
import os
from operator import itemgetter
from numpy import argmax

In [2]:
set_option("display.max_rows", 15)
pd.options.mode.chained_assignment = None

# training set is composed by databases: Repbase, RepetDB, and PGSB (consensus)
#filename = '../InpactorDB/InpactorDB_training.fasta.kmer2' 
filename = '../InpactorDB/InpactorDB_training.fasta.kmer2'
training_data = pd.read_csv(filename)
training_data

#dev and test set is composed by LTR_STRUCT database (consensus)
filename = '../InpactorDB/InpactorDB_LTR_STRUCT.fasta.kmers'
dev_test_data = pd.read_csv(filename)

In [3]:
path_log_base = './logs'
# class dist|ribution
print(training_data.groupby('Label').size())

Label
1     2330
3      404
4      403
8       22
9     1244
12    1188
13    1299
14     608
16      90
17    1494
18    2451
19    1092
20    5517
dtype: int64


In [4]:
label_vectors = training_data['Label'].values
feature_vectors = training_data.drop(['Label'], axis=1).values

label_dev_test = dev_test_data['Label'].values
feature_dev_test = dev_test_data.drop(['Label'], axis=1).values

label_vectors
feature_vectors

array([[1363,  953,  836, ...,    1,    1,    1],
       [1024,  611,  718, ...,    0,    4,    1],
       [1407, 1022,  879, ...,    2,    4,    1],
       ...,
       [1078,  925,  795, ...,    2,    1,    1],
       [1385, 1308, 1099, ...,    3,    0,    3],
       [3047, 2018, 2206, ...,   16,   20,   21]])

In [5]:
# Scaling
scaler = preprocessing.StandardScaler().fit(feature_vectors)
feature_vectors_scaler = scaler.transform(feature_vectors)

dev_test_scaler = scaler.transform(feature_dev_test)
#data split: 80% train, 10% dev and 10% test
validation_size = 0.2
seed = 7
#X_trainScaler, X_test_dev, Y_trainScaler, Y_test_dev = train_test_split(feature_vectors_scaler, label_vectors, 
                                                                                        #test_size=validation_size, 

                                                                                     #random_state=seed)

#Split data using training and dev-test sets separately option 1 (training alone and dev-test sets)

X_trainScaler = feature_vectors_scaler
Y_trainScaler = label_vectors

X_dev, X_test, Y_dev, Y_test = train_test_split(dev_test_scaler, label_dev_test, test_size=0.5, random_state=seed)

# Split data using training and dev-test sets separately option 2 (training and train-dev, and test alone)
"""X_trainScaler, X_dev, Y_trainScaler, Y_dev = train_test_split(feature_vectors_scaler, label_vectors, test_size=validation_size, random_state=seed)

X_test = dev_test_scaler
Y_test = label_dev_test"""



'X_trainScaler, X_dev, Y_trainScaler, Y_dev = train_test_split(feature_vectors_scaler, label_vectors, test_size=validation_size, random_state=seed)\n\nX_test = dev_test_scaler\nY_test = label_dev_test'

In [6]:
pca = decomposition.PCA(n_components=0.96,svd_solver='full',tol=1e-4)
pca.fit(X_trainScaler)
X_trainPCAScaler = pca.transform(X_trainScaler)
X_validationPCAScaler = pca.transform(X_dev)
X_testPCAScaler = pca.transform(X_test)

In [7]:
print(len(X_trainPCAScaler[0]))
print(X_trainPCAScaler.shape)

1902
(18142, 1902)


In [8]:
################################################## TLU ACTIVATION FUNCTION
T3 = 3;
def Tanh3(x):
    tanh3 = K.tanh(x)*T3
    return tanh3
##################################################

In [9]:
def metrics(Y_validation,predictions):
    print('Accuracy:', accuracy_score(Y_validation, predictions))
    print('F1 score:', f1_score(Y_validation, predictions,average='weighted'))
    print('Recall:', recall_score(Y_validation, predictions,average='weighted'))
    print('Precision:', precision_score(Y_validation, predictions, average='weighted'))
    print('\n clasification report:\n', classification_report(Y_validation, predictions))
    print('\n confusion matrix:\n',confusion_matrix(Y_validation, predictions))
    #Creamos la matriz de confusión
    snn_cm = confusion_matrix(Y_validation, predictions)

    # Visualizamos la matriz de confusión
    snn_df_cm = pd.DataFrame(snn_cm, range(13), range(13))  
    plt.figure(figsize = (20,14))  
    sn.set(font_scale=1.4) #for label size  
    sn.heatmap(snn_df_cm, annot=True, annot_kws={"size": 12}) # font size  
    plt.show()

In [10]:
def graphics(history, AccTest, LossTest, log_Dir, model_Name, lossTEST, lossTRAIN, lossVALID, accuracyTEST, accuracyTRAIN, accuracyVALID):
    numbers=AccTest
    numbers_sort = sorted(enumerate(numbers), key=itemgetter(1),  reverse=True)
    for i in range(int(len(numbers)*(0.05))): #5% Del total de las épocas
        index, value = numbers_sort[i]
        print("Test Accuracy {}, Época:{}\n".format(value, index+1))
    
    print("")
    
    numbers=history.history['accuracy']
    numbers_sort = sorted(enumerate(numbers), key=itemgetter(1),  reverse=True)
    for i in range(int(len(numbers)*(0.05))): #5% Del total de las épocas
        index, value = numbers_sort[i]
        print("Train Accuracy {}, Época:{}\n".format(value, index+1))
    
    print("")
    
    numbers=history.history['val_accuracy']
    numbers_sort = sorted(enumerate(numbers), key=itemgetter(1),  reverse=True)
    for i in range(int(len(numbers)*(0.05))): #5% Del total de las épocas
        index, value = numbers_sort[i]
        print("Validation Accuracy {}, Época:{}\n".format(value, index+1))

    with plt.style.context('seaborn-white'):
        plt.figure(figsize=(10, 10))
        #Plot training & validation accuracy values
        plt.plot(np.concatenate([np.array([accuracyTRAIN]),np.array(history.history['accuracy'])],axis=0))
        plt.plot(np.concatenate([np.array([accuracyVALID]),np.array(history.history['val_accuracy'])],axis=0))
        plt.plot(np.concatenate([np.array([accuracyTEST]),np.array(AccTest)],axis=0)) #Test
        plt.title('Accuracy Vs Epoch')
        plt.ylabel('Accuracy')
        plt.xlabel('Epoch')
        plt.legend(['Train', 'Validation', 'Test'], loc='upper left')
        plt.grid('on')
        #plt.savefig(path_img_base+'/Accuracy_GBRAS-Net_'+model_Name+'.eps', format='eps')
        #plt.savefig(path_img_base+'/Accuracy_GBRAS-Net_'+model_Name+'.svg', format='svg')
        #plt.savefig(path_img_base+'/Accuracy_GBRAS-Net_'+model_Name+'.pdf', format='pdf')     
        #plt.show()
        
        plt.figure(figsize=(10, 10))
        #Plot training & validation loss values
        plt.plot(np.concatenate([np.array([lossTRAIN]),np.array(history.history['loss'])],axis=0))
        plt.plot(np.concatenate([np.array([lossVALID]),np.array(history.history['val_loss'])],axis=0))
        plt.plot(np.concatenate([np.array([lossTEST]),np.array(LossTest)],axis=0)) #Test
        plt.title('Loss Vs Epoch')
        plt.ylabel('Loss')
        plt.xlabel('Epoch')
        plt.legend(['Train', 'Validation', 'Test'], loc='upper left')
        plt.grid('on')
        #plt.savefig(path_img_base+'/Loss_GBRAS-Net_'+model_Name+'.eps', format='eps')
        #plt.savefig(path_img_base+'/Loss_GBRAS-Net_'+model_Name+'.svg', format='svg')
        #plt.savefig(path_img_base+'/Loss_GBRAS-Net_'+model_Name+'.pdf', format='pdf') 
        plt.show() 

In [11]:
def Final_Results_Test(PATH_trained_models):
    global AccTest
    global LossTest
    AccTest = []
    LossTest= [] 
    B_accuracy = 0 #B --> Best
    for filename in sorted(os.listdir(PATH_trained_models)):
        if filename != ('train') and filename != ('validation'):
            print(filename)
            model = tf.keras.models.load_model(PATH_trained_models+'/'+filename, custom_objects={'Tanh3':Tanh3})
            loss,accuracy = model.evaluate(X_testPCAScaler, one_hot_labels_test,verbose=0)
            print(f'Loss={loss:.4f} y Accuracy={accuracy:0.4f}'+'\n')
            BandAccTest  = accuracy
            BandLossTest = loss
            AccTest.append(BandAccTest)    #Valores de la precisión en Test, para graficar junto a valid y train
            LossTest.append(BandLossTest)  #Valores de la perdida en Test, para graficar junto a valid y train
            
            if accuracy > B_accuracy:
                B_accuracy = accuracy
                B_loss = loss
                B_name = filename
    
    print("\n\nBest")
    print(B_name)
    print(f'Loss={B_loss:.4f} y Accuracy={B_accuracy:0.4f}'+'\n')

In [12]:
def train(model, X_train, y_train, X_valid, y_valid, X_test, y_test, batch_size, epochs, model_name=""):
    start_time = tm.time()
    log_dir=path_log_base+"/"+model_name+"_"+str(datetime.datetime.now().isoformat()[:19].replace("T", "_").replace(":","-"))
    tensorboard = tf.keras.callbacks.TensorBoard(log_dir, histogram_freq=1)
    filepath = log_dir+"/saved-model-{epoch:03d}-{val_accuracy:.4f}.hdf5"
    checkpoint = tf.keras.callbacks.ModelCheckpoint(filepath, monitor='val_accuracy', save_best_only=False, mode='max')
    model.reset_states()
    
    #VALORES EN TRAIN TEST Y VALIDACIÓN INICIALES, GRÁFICOS
    global lossTEST
    global accuracyTEST
    global lossTRAIN
    global accuracyTRAIN
    global lossVALID
    global accuracyVALID
    lossTEST,accuracyTEST   = model.evaluate(X_test, y_test,verbose=None)
    lossVALID,accuracyVALID = model.evaluate(X_valid, y_valid,verbose=None)
    lossTRAIN,accuracyTRAIN = model.evaluate(X_train, y_train,verbose=None)
    
    global history
    global model_Name
    global log_Dir
    model_Name = model_name
    log_Dir = log_dir
    
    history=model.fit(X_train, y_train, epochs=epochs, 
                      callbacks=[tensorboard,checkpoint], 
                      batch_size=batch_size,validation_data=(X_valid, y_valid),verbose=1)
    
    metrics = model.evaluate(X_test, y_test, verbose=0)
     
    TIME = tm.time() - start_time
    print("Time "+model_name+" = %s [seconds]" % TIME)
    
    print("\n")
    print(log_dir)
    return {k:v for k,v in zip (model.metrics_names, metrics)}

In [20]:
def Nakano_Net():
#def Nakano_Net(optimizer="adam"):
#def Nakano_Net(learn_rate=0.01, momentum=0):
#def Nakano_Net(dropout):
#def Nakano_Net(l1, l2):
    tf.keras.backend.clear_session()

    #Inputs
    inputs = tf.keras.Input(shape=(X_trainPCAScaler.shape[1],), name="input_1")
    #layer 1
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(inputs)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    #layer 2
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(layers)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    #layer 3
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(layers)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    #layer 4
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(layers)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    #layer 5
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(layers)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    #layer 6
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(layers)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    #layer 7
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=0, l2=0.000010))(layers)
    layers = tf.keras.layers.Dropout(0.4)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    # output
    predictions = tf.keras.layers.Dense(21, activation="softmax", name="output_1")(layers)
    # model generation
    model = tf.keras.Model(inputs = inputs, outputs=predictions)
    # optimizer
    #opt = tf.keras.optimizers.Adam(lr=0.0008, beta_1=0.7, beta_2=0.9, epsilon=1e-07)
    opt = tf.keras.optimizers.SGD(learning_rate=0.005000, momentum=0.900000)
    # loss function
    loss_fn = tf.keras.losses.CategoricalCrossentropy()
    # Compile model
    #model.compile(loss=loss_fn, optimizer=opt, metrics=['acc', 'AUC', 'mse','mae','mape'])
    model.compile(loss=loss_fn, optimizer=opt, metrics=['accuracy'])
    return model


In [14]:
# linea base, arquitectura de Nakano
# model = InpactorFNN_Net()

# arquitectura a afinar
#model = Nakano_Net()
# summarize layers
#print(model.summary())
#tf.keras.utils.plot_model(model, show_shapes=True)

one_hot_labels_train = tf.keras.utils.to_categorical(Y_trainScaler, num_classes=21)
one_hot_labels_validation = tf.keras.utils.to_categorical(Y_dev, num_classes=21)
one_hot_labels_test = tf.keras.utils.to_categorical(Y_test, num_classes=21)

In [22]:
# How to Tune Batch Size and Number of Epochs

model = tf.keras.wrappers.scikit_learn.KerasClassifier(build_fn=Nakano_Net, verbose=1)
# define the grid search parameters
batch_size = [28, 56, 128, 512]
epochs = [50, 100, 200]
param_grid = dict(batch_size=batch_size, epochs=epochs)
grid = GridSearchCV(estimator=model, param_grid=param_grid)
grid_result = grid.fit(X_trainPCAScaler, one_hot_labels_train)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/10
1452/1452 [==============================] - 3s 2ms/step - loss: 0.8187 - accuracy: 0.7573
Epoch 2/10
1452/1452 [==============================] - 2s 2ms/step - loss: 0.2275 - accuracy: 0.9408
Epoch 3/10
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1461 - accuracy: 0.9619
Epoch 4/10
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1346 - accuracy: 0.9709
Epoch 5/10
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1228 - accuracy: 0.9743
Epoch 6/10
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1117 - accuracy: 0.9755
Epoch 7/10
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1076 - accuracy: 0.9811
Epoch 8/10
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1132 - accuracy: 0.9797
Epoch 9/10
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1038 - accuracy: 0.9811
Epoch 10/10
363/363 [==============================] - 0s 1ms/step - loss: 1.2781 

1452/1452 [==============================] - 2s 2ms/step - loss: 0.1762 - accuracy: 0.9602
Epoch 5/50
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1310 - accuracy: 0.9673
Epoch 6/50
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1407 - accuracy: 0.9676
Epoch 7/50
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1295 - accuracy: 0.9724
Epoch 8/50
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1182 - accuracy: 0.9749
Epoch 9/50
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1145 - accuracy: 0.9783
Epoch 10/50
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1216 - accuracy: 0.9768
Epoch 11/50
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1139 - accuracy: 0.9807
Epoch 12/50
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1128 - accuracy: 0.9812
Epoch 13/50
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1193 - accu

1452/1452 [==============================] - 3s 2ms/step - loss: 0.0920 - accuracy: 0.9830
Epoch 11/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1088 - accuracy: 0.9832
Epoch 12/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.0902 - accuracy: 0.9838
Epoch 13/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.0827 - accuracy: 0.9874
Epoch 14/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.0977 - accuracy: 0.9864
Epoch 15/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1059 - accuracy: 0.9855
Epoch 16/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.0819 - accuracy: 0.9868
Epoch 17/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.0980 - accuracy: 0.9867
Epoch 18/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.0977 - accuracy: 0.9881
Epoch 19/100
1452/1452 [==============================] - 2s 2ms/step - loss:

1452/1452 [==============================] - 2s 2ms/step - loss: 0.1410 - accuracy: 0.9890
Epoch 67/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1230 - accuracy: 0.9906
Epoch 68/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1139 - accuracy: 0.9882
Epoch 69/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1070 - accuracy: 0.9894
Epoch 70/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1011 - accuracy: 0.9907
Epoch 71/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1135 - accuracy: 0.9919
Epoch 72/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.0997 - accuracy: 0.9912
Epoch 73/100
1452/1452 [==============================] - 3s 2ms/step - loss: 0.1493 - accuracy: 0.9912
Epoch 74/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1173 - accuracy: 0.9904
Epoch 75/100
1452/1452 [==============================] - 3s 2ms/step - loss:

1452/1452 [==============================] - 2s 2ms/step - loss: 0.1009 - accuracy: 0.9908
Epoch 45/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1314 - accuracy: 0.9892
Epoch 46/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1353 - accuracy: 0.9877
Epoch 47/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1097 - accuracy: 0.9884
Epoch 48/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.0915 - accuracy: 0.9888
Epoch 49/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1093 - accuracy: 0.9892
Epoch 50/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1296 - accuracy: 0.9887
Epoch 51/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.0873 - accuracy: 0.9896
Epoch 52/100
1452/1452 [==============================] - 2s 2ms/step - loss: 0.1077 - accuracy: 0.9904
Epoch 53/100
1452/1452 [==============================] - 2s 2ms/step - loss:

...

146/146 [==============================] - 0s 2ms/step - loss: 0.0312 - accuracy: 0.9924
Epoch 22/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0284 - accuracy: 0.9924
Epoch 23/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0324 - accuracy: 0.9919
Epoch 24/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0280 - accuracy: 0.9928
Epoch 25/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0255 - accuracy: 0.9940
Epoch 26/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0244 - accuracy: 0.9946
Epoch 27/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0253 - accuracy: 0.9935
Epoch 28/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0273 - accuracy: 0.9930
Epoch 29/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0253 - accuracy: 0.9943
Epoch 30/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0275 - accuracy: 

146/146 [==============================] - 0s 2ms/step - loss: 0.0138 - accuracy: 0.9986
Epoch 181/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0101 - accuracy: 0.9983
Epoch 182/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0159 - accuracy: 0.9982
Epoch 183/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0186 - accuracy: 0.9974
Epoch 184/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0142 - accuracy: 0.9976
Epoch 185/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0079 - accuracy: 0.9983
Epoch 186/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0162 - accuracy: 0.9979
Epoch 187/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0117 - accuracy: 0.9986
Epoch 188/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0110 - accuracy: 0.9985
Epoch 189/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0085 - a

146/146 [==============================] - 0s 2ms/step - loss: 0.0140 - accuracy: 0.9978
Epoch 140/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0180 - accuracy: 0.9973
Epoch 141/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0137 - accuracy: 0.9976
Epoch 142/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0173 - accuracy: 0.9974
Epoch 143/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0161 - accuracy: 0.9963
Epoch 144/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0114 - accuracy: 0.9980
Epoch 145/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0152 - accuracy: 0.9977
Epoch 146/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0108 - accuracy: 0.9979
Epoch 147/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0087 - accuracy: 0.9979
Epoch 148/200
146/146 [==============================] - 0s 2ms/step - loss: 0.0120 - a

363/363 [==============================] - 1s 2ms/step - loss: 0.0351 - accuracy: 0.9910
Epoch 19/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0401 - accuracy: 0.9899
Epoch 20/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0321 - accuracy: 0.9931
Epoch 21/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0366 - accuracy: 0.9917
Epoch 22/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0404 - accuracy: 0.9915
Epoch 23/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0362 - accuracy: 0.9921
Epoch 24/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0339 - accuracy: 0.9924
Epoch 25/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0367 - accuracy: 0.9926
Epoch 26/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0401 - accuracy: 0.9922
Epoch 27/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0243 - accuracy: 

363/363 [==============================] - 1s 2ms/step - loss: 0.0287 - accuracy: 0.9969
Epoch 178/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0293 - accuracy: 0.9975
Epoch 179/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0220 - accuracy: 0.9973
Epoch 180/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0299 - accuracy: 0.9966
Epoch 181/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0220 - accuracy: 0.9969
Epoch 182/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0172 - accuracy: 0.9976
Epoch 183/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0329 - accuracy: 0.9971
Epoch 184/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0258 - accuracy: 0.9973
Epoch 185/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0101 - accuracy: 0.9981
Epoch 186/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0264 - a

In [26]:
# How to Tune the Training Optimization Algorithm
# fix random seed for reproducibility
seed = 7
np.random.seed(seed)

model = KerasClassifier(build_fn=Nakano_Net, epochs=200, batch_size=50, verbose=1)
# define the grid search parameters
optimizer = ['SGD', 'RMSprop', 'Adagrad', 'Adadelta', 'Adam', 'Adamax', 'Nadam']
param_grid = dict(optimizer=optimizer)
grid = GridSearchCV(estimator=model, param_grid=param_grid)
grid_result = grid.fit(X_trainPCAScaler, one_hot_labels_train)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/200
291/291 [==============================] - 1s 2ms/step - loss: 1.7113 - accuracy: 0.5171
Epoch 2/200
291/291 [==============================] - 0s 2ms/step - loss: 0.9317 - accuracy: 0.6858
Epoch 3/200
291/291 [==============================] - 0s 2ms/step - loss: 0.6982 - accuracy: 0.7631
Epoch 4/200
291/291 [==============================] - 0s 2ms/step - loss: 0.5468 - accuracy: 0.8190
Epoch 5/200
291/291 [==============================] - 0s 2ms/step - loss: 0.4508 - accuracy: 0.8526
Epoch 6/200
291/291 [==============================] - 1s 2ms/step - loss: 0.3744 - accuracy: 0.8838
Epoch 7/200
291/291 [==============================] - 0s 2ms/step - loss: 0.3353 - accuracy: 0.8961
Epoch 8/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2829 - accuracy: 0.9125
Epoch 9/200
291/291 [==============================] - 0s 2ms/step - loss: 0.2593 - accuracy: 0.9194
Epoch 10/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2244 - accura

Epoch 81/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0191 - accuracy: 0.9943
Epoch 82/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0183 - accuracy: 0.9948
Epoch 83/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0191 - accuracy: 0.9932
Epoch 84/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0162 - accuracy: 0.9950
Epoch 85/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0175 - accuracy: 0.9952
Epoch 86/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0155 - accuracy: 0.9955
Epoch 87/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0175 - accuracy: 0.9949
Epoch 88/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0146 - accuracy: 0.9952
Epoch 89/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0186 - accuracy: 0.9943
Epoch 90/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0167

291/291 [==============================] - 1s 2ms/step - loss: 0.0807 - accuracy: 0.9762
Epoch 40/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0789 - accuracy: 0.9766
Epoch 41/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0741 - accuracy: 0.9784
Epoch 42/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0801 - accuracy: 0.9769
Epoch 43/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0726 - accuracy: 0.9771
Epoch 44/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0693 - accuracy: 0.9789
Epoch 45/200
291/291 [==============================] - 1s 2ms/step - loss: 0.0652 - accuracy: 0.9811
Epoch 46/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0689 - accuracy: 0.9806
Epoch 47/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0595 - accuracy: 0.9816
Epoch 48/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0658 - accuracy: 

291/291 [==============================] - 0s 2ms/step - loss: 0.0113 - accuracy: 0.9968
Epoch 199/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0136 - accuracy: 0.9959
Epoch 200/200
73/73 [==============================] - 0s 1ms/step - loss: 0.0460 - accuracy: 0.9956
Epoch 1/200
291/291 [==============================] - 1s 2ms/step - loss: 1.7987 - accuracy: 0.4890
Epoch 2/200
291/291 [==============================] - 1s 2ms/step - loss: 1.1006 - accuracy: 0.6462
Epoch 3/200
291/291 [==============================] - 0s 2ms/step - loss: 0.8451 - accuracy: 0.7327
Epoch 4/200
291/291 [==============================] - 0s 2ms/step - loss: 0.6881 - accuracy: 0.7835
Epoch 5/200
291/291 [==============================] - 0s 2ms/step - loss: 0.5784 - accuracy: 0.8215
Epoch 6/200
291/291 [==============================] - 1s 2ms/step - loss: 0.4888 - accuracy: 0.8523
Epoch 7/200
291/291 [==============================] - 0s 2ms/step - loss: 0.4379 - accuracy: 0.8670


291/291 [==============================] - 0s 2ms/step - loss: 0.0137 - accuracy: 0.9959
Epoch 157/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0133 - accuracy: 0.9957
Epoch 158/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0172 - accuracy: 0.9951
Epoch 159/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0174 - accuracy: 0.9949
Epoch 160/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0135 - accuracy: 0.9963
Epoch 161/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0151 - accuracy: 0.9954
Epoch 162/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0144 - accuracy: 0.9960
Epoch 163/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0155 - accuracy: 0.9957
Epoch 164/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0154 - accuracy: 0.9960
Epoch 165/200
291/291 [==============================] - 0s 2ms/step - loss: 0.0115 - a

...

291/291 [==============================] - 1s 3ms/step - loss: 0.0238 - accuracy: 0.9977
Epoch 182/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0298 - accuracy: 0.9982
Epoch 183/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0195 - accuracy: 0.9970
Epoch 184/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0205 - accuracy: 0.9979
Epoch 185/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0233 - accuracy: 0.9975
Epoch 186/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0154 - accuracy: 0.9976
Epoch 187/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0259 - accuracy: 0.9977
Epoch 188/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0281 - accuracy: 0.9969
Epoch 189/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0199 - accuracy: 0.9977
Epoch 190/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0111 - a

291/291 [==============================] - 1s 3ms/step - loss: 0.0214 - accuracy: 0.9966
Epoch 141/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0175 - accuracy: 0.9975
Epoch 142/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0226 - accuracy: 0.9976
Epoch 143/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0207 - accuracy: 0.9972
Epoch 144/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0341 - accuracy: 0.9970
Epoch 145/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0191 - accuracy: 0.9972
Epoch 146/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0278 - accuracy: 0.9970
Epoch 147/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0256 - accuracy: 0.9970
Epoch 148/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0206 - accuracy: 0.9977
Epoch 149/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0197 - a

291/291 [==============================] - 1s 3ms/step - loss: 0.0414 - accuracy: 0.9896
Epoch 20/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0449 - accuracy: 0.9899
Epoch 21/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0401 - accuracy: 0.9891
Epoch 22/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0334 - accuracy: 0.9916
Epoch 23/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0479 - accuracy: 0.9890
Epoch 24/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0311 - accuracy: 0.9919
Epoch 25/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0397 - accuracy: 0.9912
Epoch 26/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0455 - accuracy: 0.9891
Epoch 27/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0349 - accuracy: 0.9915
Epoch 28/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0357 - accuracy: 

291/291 [==============================] - 1s 3ms/step - loss: 0.0257 - accuracy: 0.9973
Epoch 179/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0254 - accuracy: 0.9968
Epoch 180/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0221 - accuracy: 0.9975
Epoch 181/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0399 - accuracy: 0.9966
Epoch 182/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0182 - accuracy: 0.9979
Epoch 183/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0221 - accuracy: 0.9972
Epoch 184/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0159 - accuracy: 0.9977
Epoch 185/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0215 - accuracy: 0.9977
Epoch 186/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0263 - accuracy: 0.9973
Epoch 187/200
291/291 [==============================] - 1s 3ms/step - loss: 0.0227 - a

363/363 [==============================] - 1s 2ms/step - loss: 0.0142 - accuracy: 0.9956
Epoch 138/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0161 - accuracy: 0.9954
Epoch 139/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0173 - accuracy: 0.9957
Epoch 140/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0152 - accuracy: 0.9951
Epoch 141/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0157 - accuracy: 0.9955
Epoch 142/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0147 - accuracy: 0.9955
Epoch 143/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0153 - accuracy: 0.9958
Epoch 144/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0134 - accuracy: 0.9961
Epoch 145/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0129 - accuracy: 0.9960
Epoch 146/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0131 - a

In [28]:
# How to Tune Learning Rate and Momentum
seed = 7
np.random.seed(seed)

model = KerasClassifier(build_fn=Nakano_Net, epochs=200, batch_size=50, verbose=1)
# define the grid search parameters
learn_rate = [0.001, 0.01, 0.1, 0.2, 0.3]
momentum = [0.0, 0.2, 0.4, 0.6, 0.8, 0.9]
param_grid = dict(learn_rate=learn_rate, momentum=momentum)
grid = GridSearchCV(estimator=model, param_grid=param_grid)
grid_result = grid.fit(X_trainPCAScaler, one_hot_labels_train)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

Epoch 1/200
291/291 [==============================] - 1s 2ms/step - loss: 3.0670 - accuracy: 0.3021
Epoch 2/200
291/291 [==============================] - 0s 2ms/step - loss: 2.1671 - accuracy: 0.4068
Epoch 3/200
291/291 [==============================] - 0s 2ms/step - loss: 1.8402 - accuracy: 0.4632
Epoch 4/200
291/291 [==============================] - 0s 2ms/step - loss: 1.6342 - accuracy: 0.5112
Epoch 5/200
291/291 [==============================] - 1s 2ms/step - loss: 1.4859 - accuracy: 0.5425
Epoch 6/200
291/291 [==============================] - 1s 2ms/step - loss: 1.3808 - accuracy: 0.5689
Epoch 7/200
291/291 [==============================] - 0s 2ms/step - loss: 1.2992 - accuracy: 0.5875
Epoch 8/200
291/291 [==============================] - 0s 2ms/step - loss: 1.2175 - accuracy: 0.6104
Epoch 9/200
291/291 [==============================] - 1s 2ms/step - loss: 1.1588 - accuracy: 0.6302
Epoch 10/200
291/291 [==============================] - 1s 2ms/step - loss: 1.1048 - accura

291/291 [==============================] - 1s 2ms/step - loss: 0.1165 - accuracy: 0.9649
Epoch 161/200
291/291 [==============================] - 1s 2ms/step - loss: 0.1097 - accuracy: 0.9694
Epoch 162/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1111 - accuracy: 0.9660
Epoch 163/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1107 - accuracy: 0.9690
Epoch 164/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1069 - accuracy: 0.9691
Epoch 165/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1116 - accuracy: 0.9681
Epoch 166/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1069 - accuracy: 0.9688
Epoch 167/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1059 - accuracy: 0.9667
Epoch 168/200
291/291 [==============================] - 0s 2ms/step - loss: 0.1009 - accuracy: 0.9691
Epoch 169/200
291/291 [==============================] - 1s 2ms/step - loss: 0.1019 - a

291/291 [==============================] - 1s 2ms/step - loss: 0.2403 - accuracy: 0.9272
Epoch 118/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2339 - accuracy: 0.9315
Epoch 119/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2320 - accuracy: 0.9312
Epoch 120/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2297 - accuracy: 0.9312
Epoch 121/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2285 - accuracy: 0.9319
Epoch 122/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2300 - accuracy: 0.9327
Epoch 123/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2195 - accuracy: 0.9350
Epoch 124/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2284 - accuracy: 0.9319
Epoch 125/200
291/291 [==============================] - 0s 2ms/step - loss: 0.2252 - accuracy: 0.9330
Epoch 126/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2214 - a

291/291 [==============================] - 0s 2ms/step - loss: 0.3289 - accuracy: 0.9061
Epoch 76/200
291/291 [==============================] - 1s 2ms/step - loss: 0.3256 - accuracy: 0.9054
Epoch 77/200
291/291 [==============================] - 0s 2ms/step - loss: 0.3202 - accuracy: 0.9024
Epoch 78/200
291/291 [==============================] - 1s 2ms/step - loss: 0.3162 - accuracy: 0.9085
Epoch 79/200
291/291 [==============================] - 0s 2ms/step - loss: 0.3070 - accuracy: 0.9117
Epoch 80/200
291/291 [==============================] - 0s 2ms/step - loss: 0.3080 - accuracy: 0.9118
Epoch 81/200
291/291 [==============================] - 0s 2ms/step - loss: 0.3008 - accuracy: 0.9104
Epoch 82/200
291/291 [==============================] - 0s 2ms/step - loss: 0.2946 - accuracy: 0.9147
Epoch 83/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2981 - accuracy: 0.9112
Epoch 84/200
291/291 [==============================] - 1s 2ms/step - loss: 0.2876 - accuracy: 

291/291 [==============================] - 0s 2ms/step - loss: 0.6649 - accuracy: 0.7946
Epoch 34/200
291/291 [==============================] - 1s 2ms/step - loss: 0.6461 - accuracy: 0.7972
Epoch 35/200
291/291 [==============================] - 1s 2ms/step - loss: 0.6490 - accuracy: 0.7991
Epoch 36/200
291/291 [==============================] - 1s 2ms/step - loss: 0.6129 - accuracy: 0.8100
Epoch 37/200
291/291 [==============================] - 1s 2ms/step - loss: 0.6069 - accuracy: 0.8100
Epoch 38/200
291/291 [==============================] - 1s 2ms/step - loss: 0.5998 - accuracy: 0.8159
Epoch 39/200
291/291 [==============================] - 1s 2ms/step - loss: 0.5764 - accuracy: 0.8227
Epoch 40/200
291/291 [==============================] - 1s 2ms/step - loss: 0.5681 - accuracy: 0.8267
Epoch 41/200
291/291 [==============================] - 1s 2ms/step - loss: 0.5598 - accuracy: 0.8271
Epoch 42/200
291/291 [==============================] - 1s 2ms/step - loss: 0.5573 - accuracy: 

...

291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 76/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 77/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 78/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 79/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 80/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 81/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 82/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 83/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 84/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accu

291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 33/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 34/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 35/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 36/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 37/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 38/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 39/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 40/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 41/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accu

291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 190/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 191/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 192/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 193/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 194/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 195/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 196/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 197/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 198/200
291/291 [==============================] - 1s 2ms/step - loss: n

291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 147/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 148/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 149/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 150/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 151/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 152/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 153/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 154/200
291/291 [==============================] - 1s 2ms/step - loss: nan - accuracy: 0.0000e+00
Epoch 155/200
291/291 [==============================] - 0s 2ms/step - loss: n

363/363 [==============================] - 1s 2ms/step - loss: 0.0219 - accuracy: 0.9936
Epoch 105/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0203 - accuracy: 0.9943
Epoch 106/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0256 - accuracy: 0.9921
Epoch 107/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0242 - accuracy: 0.9931
Epoch 108/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0202 - accuracy: 0.9947
Epoch 109/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0187 - accuracy: 0.9939
Epoch 110/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0201 - accuracy: 0.9945
Epoch 111/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0194 - accuracy: 0.9944
Epoch 112/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0170 - accuracy: 0.9950
Epoch 113/200
363/363 [==============================] - 1s 2ms/step - loss: 0.0178 - a

In [77]:
## Afinando la arquitectura
def create_fnn(layer_sizes):
    model = Sequential()
    model.add(tf.keras.Input(shape=(X_trainPCAScaler.shape[1],), name="input_1"))
    #model.add(Dense(layer_sizes[0], input_dim=X_trainPCAScaler.shape[1], activation='relu'))
    #model.add(Dropout(0.4))
    #model.add(BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None))
        
    for s in layer_sizes:
        model.add(Dense(units = s, activation = 'relu', kernel_regularizer=regularizers.l1_l2(l1=0.00001, l2=0)))
        model.add(Dropout(0.4))
        model.add(BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None))
    model.add(Dense(units=21, activation='softmax'))
    opt = tf.keras.optimizers.Adam(lr=0.0008, beta_1=0.7, beta_2=0.9, epsilon=1e-07)
    loss_fn = tf.keras.losses.CategoricalCrossentropy()
    model.compile(loss=loss_fn, optimizer=opt, metrics=['accuracy'])
    return model

In [15]:
# tuning by search Grid: lr=0.001, momentum=0.9, epochs=200, batch_size=50, optimizer = SGD
def evaluate(model, batch_size, epochs, X_train, y_train, X_val, y_val, X_test, y_test):
    model.summary()
    optimizer = tf.keras.optimizers.SGD(lr=0.001, momentum=0.9) # tuning by search Grid
    model.compile(optimizer=optimizer, loss='categorical_crossentropy', metrics=['accuracy'])
    model.fit(X_train, y_train, validation_data=(X_val, y_val), epochs=epochs, batch_size=batch_size, verbose=2) 
    scores = model.evaluate(X_test, y_test, verbose=0)
    print("Baseline Error: %.2f%%" % (100-scores[1]*100))

In [18]:
batch_size = [28, 56, 128, 512]
epochs = [50, 100, 200]

errors = []
bs = []
es = []

for i in batch_size:
    for j in epochs:
        model = Nakano_Net()
        error = evaluate(model, i, j, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
        errors.append(error)
        bs.append(i)
        es.append(j)


print("best error: %f" %(min(errors)))        

for error, e, m in zip(errors, bs, es):
    print("%f with: %d, %d" % (error, e, m))
    
# best error: 16.768754 with: 56, 50

Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 1902)]            0         
_________________________________________________________________
dense (Dense)                (None, 500)               951500    
_________________________________________________________________
dropout (Dropout)            (None, 500)               0         
_________________________________________________________________
batch_normalization (BatchNo (None, 500)               1500      
_________________________________________________________________
dense_1 (Dense)              (None, 500)               250500    
_________________________________________________________________
dropout_1 (Dropout)          (None, 500)               0         
_________________________________________________________________
batch_normalization_1 (Batch (None, 500)               1500  

Epoch 45/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6521 - accuracy: 0.9754
Epoch 46/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6557 - accuracy: 0.9746
Epoch 47/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6601 - accuracy: 0.9743
Epoch 48/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6582 - accuracy: 0.9738
Epoch 49/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6692 - accuracy: 0.9738
Epoch 50/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6540 - accuracy: 0.9750
Epoch 51/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6632 - accuracy: 0.9740
Epoch 52/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6615 - accuracy: 0.9745
Epoch 53/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6531 - accuracy: 0.9772
Epoch 54/100
648/648 [==============================] - 4s 6ms/step - loss: 0.6581

Epoch 1/200
648/648 [==============================] - 4s 6ms/step - loss: 2.2797 - accuracy: 0.5715
Epoch 2/200
648/648 [==============================] - 4s 6ms/step - loss: 1.3119 - accuracy: 0.8739
Epoch 3/200
648/648 [==============================] - 4s 6ms/step - loss: 1.1492 - accuracy: 0.9224
Epoch 4/200
648/648 [==============================] - 4s 6ms/step - loss: 1.0530 - accuracy: 0.9414
Epoch 5/200
648/648 [==============================] - 4s 6ms/step - loss: 0.9812 - accuracy: 0.9520
Epoch 6/200
648/648 [==============================] - 4s 6ms/step - loss: 0.9328 - accuracy: 0.9563
Epoch 7/200
648/648 [==============================] - 4s 6ms/step - loss: 0.8859 - accuracy: 0.9614
Epoch 8/200
648/648 [==============================] - 4s 6ms/step - loss: 0.8590 - accuracy: 0.9617
Epoch 9/200
648/648 [==============================] - 4s 6ms/step - loss: 0.8300 - accuracy: 0.9640
Epoch 10/200
648/648 [==============================] - 4s 6ms/step - loss: 0.7931 - accura

648/648 [==============================] - 4s 6ms/step - loss: 0.6584 - accuracy: 0.9777
Epoch 161/200
648/648 [==============================] - 4s 6ms/step - loss: 0.6547 - accuracy: 0.9787
Epoch 162/200
648/648 [==============================] - 4s 6ms/step - loss: 0.6616 - accuracy: 0.9773
Epoch 163/200
648/648 [==============================] - 4s 6ms/step - loss: 0.6491 - accuracy: 0.9784
Epoch 164/200
648/648 [==============================] - 4s 6ms/step - loss: 0.6430 - accuracy: 0.9777
Epoch 165/200
648/648 [==============================] - 4s 6ms/step - loss: 0.6375 - accuracy: 0.9786
Epoch 166/200
648/648 [==============================] - 3s 5ms/step - loss: 0.6491 - accuracy: 0.9787
Epoch 167/200
648/648 [==============================] - 4s 5ms/step - loss: 0.6499 - accuracy: 0.9781
Epoch 168/200
648/648 [==============================] - 4s 5ms/step - loss: 0.6474 - accuracy: 0.9781
Epoch 169/200
648/648 [==============================] - 4s 5ms/step - loss: 0.6482 - a

324/324 [==============================] - 2s 5ms/step - loss: 1.0277 - accuracy: 0.9425
Epoch 4/100
324/324 [==============================] - 2s 5ms/step - loss: 0.9393 - accuracy: 0.9578
Epoch 5/100
324/324 [==============================] - 2s 5ms/step - loss: 0.8745 - accuracy: 0.9653
Epoch 6/100
324/324 [==============================] - 2s 5ms/step - loss: 0.8089 - accuracy: 0.9727
Epoch 7/100
324/324 [==============================] - 2s 5ms/step - loss: 0.7566 - accuracy: 0.9751
Epoch 8/100
324/324 [==============================] - 2s 5ms/step - loss: 0.7069 - accuracy: 0.9771
Epoch 9/100
324/324 [==============================] - 2s 5ms/step - loss: 0.6788 - accuracy: 0.9776
Epoch 10/100
324/324 [==============================] - 2s 6ms/step - loss: 0.6508 - accuracy: 0.9778
Epoch 11/100
324/324 [==============================] - 2s 6ms/step - loss: 0.6248 - accuracy: 0.9813
Epoch 12/100
324/324 [==============================] - 2s 5ms/step - loss: 0.6071 - accuracy: 0.9788

...

Epoch 1/200
142/142 [==============================] - 1s 5ms/step - loss: 2.5540 - accuracy: 0.4756
Epoch 2/200
142/142 [==============================] - 1s 6ms/step - loss: 1.3678 - accuracy: 0.8319
Epoch 3/200
142/142 [==============================] - 1s 6ms/step - loss: 1.0471 - accuracy: 0.9347
Epoch 4/200
142/142 [==============================] - 1s 6ms/step - loss: 0.9305 - accuracy: 0.9611
Epoch 5/200
142/142 [==============================] - 1s 6ms/step - loss: 0.8683 - accuracy: 0.9708
Epoch 6/200
142/142 [==============================] - 1s 6ms/step - loss: 0.8110 - accuracy: 0.9776
Epoch 7/200
142/142 [==============================] - 1s 6ms/step - loss: 0.7606 - accuracy: 0.9796
Epoch 8/200
142/142 [==============================] - 1s 6ms/step - loss: 0.7101 - accuracy: 0.9848
Epoch 9/200
142/142 [==============================] - 1s 6ms/step - loss: 0.6693 - accuracy: 0.9842
Epoch 10/200
142/142 [==============================] - 1s 5ms/step - loss: 0.6303 - accura

142/142 [==============================] - 1s 6ms/step - loss: 0.3061 - accuracy: 0.9924
Epoch 161/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3021 - accuracy: 0.9922
Epoch 162/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3020 - accuracy: 0.9919
Epoch 163/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3034 - accuracy: 0.9926
Epoch 164/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3053 - accuracy: 0.9914
Epoch 165/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3107 - accuracy: 0.9905
Epoch 166/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3046 - accuracy: 0.9921
Epoch 167/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3026 - accuracy: 0.9917
Epoch 168/200
142/142 [==============================] - 1s 6ms/step - loss: 0.2970 - accuracy: 0.9929
Epoch 169/200
142/142 [==============================] - 1s 6ms/step - loss: 0.3027 - a

36/36 [==============================] - 0s 6ms/step - loss: 1.1772 - accuracy: 0.8884
Epoch 5/100
36/36 [==============================] - 0s 6ms/step - loss: 1.0097 - accuracy: 0.9411
Epoch 6/100
36/36 [==============================] - 0s 6ms/step - loss: 0.9261 - accuracy: 0.9623
Epoch 7/100
36/36 [==============================] - 0s 6ms/step - loss: 0.8746 - accuracy: 0.9712
Epoch 8/100
36/36 [==============================] - 0s 6ms/step - loss: 0.8309 - accuracy: 0.9799
Epoch 9/100
36/36 [==============================] - 0s 6ms/step - loss: 0.7953 - accuracy: 0.9851
Epoch 10/100
36/36 [==============================] - 0s 6ms/step - loss: 0.7718 - accuracy: 0.9854
Epoch 11/100
36/36 [==============================] - 0s 6ms/step - loss: 0.7374 - accuracy: 0.9888
Epoch 12/100
36/36 [==============================] - 0s 6ms/step - loss: 0.7101 - accuracy: 0.9910
Epoch 13/100
36/36 [==============================] - 0s 6ms/step - loss: 0.6881 - accuracy: 0.9904
Epoch 14/100
36/36

36/36 [==============================] - 0s 5ms/step - loss: 0.2102 - accuracy: 0.9960
Epoch 87/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2082 - accuracy: 0.9962
Epoch 88/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2148 - accuracy: 0.9954
Epoch 89/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2080 - accuracy: 0.9970
Epoch 90/100
36/36 [==============================] - 0s 5ms/step - loss: 0.2146 - accuracy: 0.9956
Epoch 91/100
36/36 [==============================] - 0s 5ms/step - loss: 0.2105 - accuracy: 0.9961
Epoch 92/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2089 - accuracy: 0.9970
Epoch 93/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2075 - accuracy: 0.9954
Epoch 94/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2061 - accuracy: 0.9971
Epoch 95/100
36/36 [==============================] - 0s 6ms/step - loss: 0.2081 - accuracy: 0.9960
Epoch 96/100


36/36 [==============================] - 0s 6ms/step - loss: 0.1987 - accuracy: 0.9968
Epoch 115/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1962 - accuracy: 0.9970
Epoch 116/200
36/36 [==============================] - 0s 6ms/step - loss: 0.2016 - accuracy: 0.9961
Epoch 117/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1990 - accuracy: 0.9968
Epoch 118/200
36/36 [==============================] - 0s 6ms/step - loss: 0.2068 - accuracy: 0.9956
Epoch 119/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1956 - accuracy: 0.9974
Epoch 120/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1962 - accuracy: 0.9970
Epoch 121/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1986 - accuracy: 0.9964
Epoch 122/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1968 - accuracy: 0.9964
Epoch 123/200
36/36 [==============================] - 0s 6ms/step - loss: 0.1971 - accuracy: 0.9963
Epoc

In [78]:
num_nodes_per_layer = [x for x in range(100, 1000, 100)]
num_layers = [x for x in range(1, 31)]

errors = []
lays = []

for layers in num_layers:
    model = create_fnn([500] * layers)
    error = evaluate(model, 56, 200, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
    errors.append(error)
    lays.append(layers)


print("best error: %f" %(min(errors)))        

for error, l1i in zip(errors, lays):
    print("%f with: %d" % (error, l1i))    
#best error 15.694630 with: 7 layers

Model: "sequential_10"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_486 (Dense)            (None, 500)               951500    
_________________________________________________________________
dropout_471 (Dropout)        (None, 500)               0         
_________________________________________________________________
batch_normalization_469 (Bat (None, 500)               1500      
_________________________________________________________________
dense_487 (Dense)            (None, 21)                10521     
Total params: 963,521
Trainable params: 962,521
Non-trainable params: 1,000
_________________________________________________________________
Epoch 1/200
324/324 [==============================] - 1s 2ms/step - loss: 0.5940 - accuracy: 0.9086
Epoch 2/200
324/324 [==============================] - 1s 2ms/step - loss: 0.2416 - accuracy: 0.9902
Epoch 3/200
324/324 [==================

324/324 [==============================] - 1s 2ms/step - loss: 0.0875 - accuracy: 0.9970
Epoch 152/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0865 - accuracy: 0.9966
Epoch 153/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0783 - accuracy: 0.9976
Epoch 154/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0794 - accuracy: 0.9965
Epoch 155/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0944 - accuracy: 0.9954
Epoch 156/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0891 - accuracy: 0.9967
Epoch 157/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0878 - accuracy: 0.9964
Epoch 158/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0887 - accuracy: 0.9966
Epoch 159/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0820 - accuracy: 0.9975
Epoch 160/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0793 - a

324/324 [==============================] - 1s 3ms/step - loss: 0.1731 - accuracy: 0.9939
Epoch 19/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1798 - accuracy: 0.9927
Epoch 20/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1728 - accuracy: 0.9940
Epoch 21/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1749 - accuracy: 0.9934
Epoch 22/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1744 - accuracy: 0.9933
Epoch 23/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1713 - accuracy: 0.9944
Epoch 24/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1676 - accuracy: 0.9944
Epoch 25/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1693 - accuracy: 0.9945
Epoch 26/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1777 - accuracy: 0.9923
Epoch 27/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1669 - accuracy: 

324/324 [==============================] - 1s 3ms/step - loss: 0.1379 - accuracy: 0.9942
Epoch 178/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1345 - accuracy: 0.9955
Epoch 179/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1447 - accuracy: 0.9939
Epoch 180/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1386 - accuracy: 0.9948
Epoch 181/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1427 - accuracy: 0.9936
Epoch 182/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1427 - accuracy: 0.9949
Epoch 183/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1387 - accuracy: 0.9948
Epoch 184/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1312 - accuracy: 0.9955
Epoch 185/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1362 - accuracy: 0.9950
Epoch 186/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1347 - a

324/324 [==============================] - 1s 3ms/step - loss: 0.1994 - accuracy: 0.9939
Epoch 121/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2140 - accuracy: 0.9917
Epoch 122/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2048 - accuracy: 0.9926
Epoch 123/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2027 - accuracy: 0.9928
Epoch 124/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2025 - accuracy: 0.9928
Epoch 125/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2049 - accuracy: 0.9928
Epoch 126/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1956 - accuracy: 0.9935
Epoch 127/200
324/324 [==============================] - 1s 3ms/step - loss: 0.1952 - accuracy: 0.9932
Epoch 128/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2005 - accuracy: 0.9927
Epoch 129/200
324/324 [==============================] - 1s 3ms/step - loss: 0.2083 - a

...

324/324 [==============================] - 5s 16ms/step - loss: 1.8359 - accuracy: 0.6457
Epoch 160/200
324/324 [==============================] - 5s 15ms/step - loss: 1.8258 - accuracy: 0.6413
Epoch 161/200
324/324 [==============================] - 5s 15ms/step - loss: 1.8505 - accuracy: 0.6350
Epoch 162/200
324/324 [==============================] - 5s 15ms/step - loss: 1.8418 - accuracy: 0.6449
Epoch 163/200
324/324 [==============================] - 5s 16ms/step - loss: 1.8333 - accuracy: 0.6396
Epoch 164/200
324/324 [==============================] - 5s 16ms/step - loss: 1.8591 - accuracy: 0.6341
Epoch 165/200
324/324 [==============================] - 5s 15ms/step - loss: 1.8338 - accuracy: 0.6347
Epoch 166/200
324/324 [==============================] - 5s 15ms/step - loss: 1.8282 - accuracy: 0.6450
Epoch 167/200
324/324 [==============================] - 5s 15ms/step - loss: 1.8399 - accuracy: 0.6338
Epoch 168/200
324/324 [==============================] - 5s 15ms/step - loss: 

324/324 [==============================] - 5s 16ms/step - loss: 5.9153 - accuracy: 0.1686
Epoch 2/200
324/324 [==============================] - 5s 16ms/step - loss: 5.4857 - accuracy: 0.2330
Epoch 3/200
324/324 [==============================] - 5s 15ms/step - loss: 5.4486 - accuracy: 0.2698
Epoch 4/200
324/324 [==============================] - 5s 15ms/step - loss: 5.3346 - accuracy: 0.2963
Epoch 5/200
324/324 [==============================] - 5s 15ms/step - loss: 4.9249 - accuracy: 0.4179
Epoch 6/200
324/324 [==============================] - 5s 15ms/step - loss: 4.4018 - accuracy: 0.5039
Epoch 7/200
324/324 [==============================] - 5s 15ms/step - loss: 3.8469 - accuracy: 0.5022
Epoch 8/200
324/324 [==============================] - 5s 15ms/step - loss: 3.5041 - accuracy: 0.4902
Epoch 9/200
324/324 [==============================] - 5s 15ms/step - loss: 3.3034 - accuracy: 0.4991
Epoch 10/200
324/324 [==============================] - 5s 16ms/step - loss: 3.1625 - accuracy

324/324 [==============================] - 5s 16ms/step - loss: 1.9341 - accuracy: 0.6375
Epoch 160/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9240 - accuracy: 0.6444
Epoch 161/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9112 - accuracy: 0.6422
Epoch 162/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9333 - accuracy: 0.6420
Epoch 163/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9554 - accuracy: 0.6307
Epoch 164/200
324/324 [==============================] - 5s 16ms/step - loss: 1.8946 - accuracy: 0.6343
Epoch 165/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9010 - accuracy: 0.6425
Epoch 166/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9145 - accuracy: 0.6461
Epoch 167/200
324/324 [==============================] - 5s 15ms/step - loss: 1.9199 - accuracy: 0.6430
Epoch 168/200
324/324 [==============================] - 5s 16ms/step - loss: 

324/324 [==============================] - 5s 16ms/step - loss: 6.0279 - accuracy: 0.1721
Epoch 2/200
324/324 [==============================] - 5s 16ms/step - loss: 5.5838 - accuracy: 0.2310
Epoch 3/200
324/324 [==============================] - 5s 16ms/step - loss: 5.5315 - accuracy: 0.2673
Epoch 4/200
324/324 [==============================] - 5s 16ms/step - loss: 5.3774 - accuracy: 0.3015
Epoch 5/200
324/324 [==============================] - 5s 16ms/step - loss: 4.8946 - accuracy: 0.4429
Epoch 6/200
324/324 [==============================] - 5s 16ms/step - loss: 4.3075 - accuracy: 0.5026
Epoch 7/200
324/324 [==============================] - 5s 16ms/step - loss: 3.8282 - accuracy: 0.4976
Epoch 8/200
324/324 [==============================] - 5s 16ms/step - loss: 3.6700 - accuracy: 0.4774
Epoch 9/200
324/324 [==============================] - 5s 17ms/step - loss: 3.4668 - accuracy: 0.4740
Epoch 10/200
324/324 [==============================] - 5s 17ms/step - loss: 3.2373 - accuracy

324/324 [==============================] - 5s 16ms/step - loss: 1.9627 - accuracy: 0.6343
Epoch 160/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9506 - accuracy: 0.6407
Epoch 161/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9543 - accuracy: 0.6416
Epoch 162/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9380 - accuracy: 0.6402
Epoch 163/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9946 - accuracy: 0.6333
Epoch 164/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9721 - accuracy: 0.6417
Epoch 165/200
324/324 [==============================] - 5s 17ms/step - loss: 1.9271 - accuracy: 0.6409
Epoch 166/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9684 - accuracy: 0.6357
Epoch 167/200
324/324 [==============================] - 5s 16ms/step - loss: 1.9625 - accuracy: 0.6297
Epoch 168/200
324/324 [==============================] - 5s 16ms/step - loss: 

In [30]:
## Afinando L1_L2
#def create_fnn(l1, l2):
#def create_fnn(drop):
#def create_fnn(momentum):
#def create_fnn(optimizer):
#def create_fnn(lr, b1, b2):
def create_fnn():
    inputs = tf.keras.Input(shape=(X_trainPCAScaler.shape[1],), name="input_1")
    #layer 1
    layers = tf.keras.layers.Dense(500,activation="relu", kernel_regularizer=regularizers.l1_l2(l1=1e-5, l2=1e-5))(inputs)
    layers = tf.keras.layers.Dropout(0.5)(layers)
    layers = tf.keras.layers.BatchNormalization(momentum=0.8, epsilon=0.001, center=True, scale=False, trainable=True, fused=None, renorm=False, renorm_clipping=None, renorm_momentum=0.4, adjustment=None)(layers)
    predictions = tf.keras.layers.Dense(21, activation="softmax", name="output_1")(layers)
    # model generation
    model = tf.keras.Model(inputs = inputs, outputs=predictions)
    # optimizer 
    opt = tf.keras.optimizers.Adam(lr=0.000800, beta_1=0.700000, beta_2=0.900000, epsilon=1e-07)
    # loss function
    loss_fn = tf.keras.losses.CategoricalCrossentropy()
    # Compile model
    #model.compile(loss=loss_fn, optimizer=opt, metrics=['acc', 'AUC', 'mse','mae','mape'])
    model.compile(loss=loss_fn, optimizer=opt, metrics=['accuracy'])
    return model

In [15]:
# tuning by search Grid: lr=0.001, momentum=0.9, epochs=200, batch_size=50, optimizer = SGD
def evaluate(model, batch_size, epochs, X_train, y_train, X_val, y_val):
    model.summary()
    model.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, verbose=1) 
    scores = model.evaluate(X_val, y_val, verbose=0)
    error = 100-scores[1]*100
    print("base error: "+str(error))
    return error

In [18]:
# define the grid search parameters L1 L2
seed = 7
np.random.seed(seed)
errors = []
l1s = []
l2s = []

l1 = [1e-5, 1e-3, 1e-1, 1e-7, 1e-9]
l2 = [1e-5, 1e-3, 1e-1, 1e-7, 1e-9]

for i in l1:
    for j in l2:
        model = Nakano_Net(i, j)
        error = evaluate(model, 56, 50, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
        errors.append(error)
        l1s.append(i)
        l2s.append(j)

print("best error: %f" %(min(errors)))        

for error, l1i, l2j in zip(errors, l1s, l2s):
    print("%f with: %f and %f" % (error, l1i, l2j))
    
# best error: best error: 15.392810 with l1=1e-5 and l2=1e-5

Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 1902)]            0         
_________________________________________________________________
dense (Dense)                (None, 500)               951500    
_________________________________________________________________
dropout (Dropout)            (None, 500)               0         
_________________________________________________________________
batch_normalization (BatchNo (None, 500)               1500      
_________________________________________________________________
dense_1 (Dense)              (None, 500)               250500    
_________________________________________________________________
dropout_1 (Dropout)          (None, 500)               0         
_________________________________________________________________
batch_normalization_1 (Batch (None, 500)               1500  

324/324 [==============================] - 2s 6ms/step - loss: 0.5515 - accuracy: 0.9735
Epoch 46/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5395 - accuracy: 0.9753
Epoch 47/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5561 - accuracy: 0.9728
Epoch 48/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5427 - accuracy: 0.9751
Epoch 49/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5203 - accuracy: 0.9770
Epoch 50/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5356 - accuracy: 0.9740
base error: 19.529515504837036
Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 1902)]            0         
_________________________________________________________________
dense (Dense)                (None, 500)               951500    
______________________________

Epoch 42/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7663 - accuracy: 0.9015
Epoch 43/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7764 - accuracy: 0.8983
Epoch 44/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7956 - accuracy: 0.9024
Epoch 45/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7294 - accuracy: 0.8994
Epoch 46/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7091 - accuracy: 0.9052
Epoch 47/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7312 - accuracy: 0.9021
Epoch 48/50
324/324 [==============================] - 2s 6ms/step - loss: 1.6685 - accuracy: 0.9057
Epoch 49/50
324/324 [==============================] - 2s 6ms/step - loss: 1.7113 - accuracy: 0.9038
Epoch 50/50
324/324 [==============================] - 2s 6ms/step - loss: 1.6840 - accuracy: 0.9023
base error: 27.04837918281555
Model: "model"
______________________________________________

324/324 [==============================] - 2s 6ms/step - loss: 0.3328 - accuracy: 0.9907
Epoch 37/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3198 - accuracy: 0.9900
Epoch 38/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3259 - accuracy: 0.9889
Epoch 39/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3241 - accuracy: 0.9900
Epoch 40/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3172 - accuracy: 0.9901
Epoch 41/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3188 - accuracy: 0.9897
Epoch 42/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3107 - accuracy: 0.9911
Epoch 43/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3077 - accuracy: 0.9899
Epoch 44/50
324/324 [==============================] - 2s 6ms/step - loss: 0.3017 - accuracy: 0.9905
Epoch 45/50
324/324 [==============================] - 2s 6ms/step - loss: 0.2942 - accuracy: 0.9916
Ep

324/324 [==============================] - 2s 6ms/step - loss: 2.2538 - accuracy: 0.9234
Epoch 31/50
324/324 [==============================] - 2s 6ms/step - loss: 2.2288 - accuracy: 0.9269
Epoch 32/50
324/324 [==============================] - 2s 6ms/step - loss: 2.1866 - accuracy: 0.9280
Epoch 33/50
324/324 [==============================] - 2s 6ms/step - loss: 2.2006 - accuracy: 0.9284
Epoch 34/50
324/324 [==============================] - 2s 6ms/step - loss: 2.1651 - accuracy: 0.9282
Epoch 35/50
324/324 [==============================] - 2s 6ms/step - loss: 2.1254 - accuracy: 0.9290
Epoch 36/50
324/324 [==============================] - 2s 6ms/step - loss: 2.1167 - accuracy: 0.9302
Epoch 37/50
324/324 [==============================] - 2s 6ms/step - loss: 2.0949 - accuracy: 0.9282
Epoch 38/50
324/324 [==============================] - 2s 6ms/step - loss: 2.1157 - accuracy: 0.9294
Epoch 39/50
324/324 [==============================] - 2s 6ms/step - loss: 2.0798 - accuracy: 0.9309
Ep

...

Epoch 1/50
324/324 [==============================] - 2s 6ms/step - loss: 0.7187 - accuracy: 0.8124
Epoch 2/50
324/324 [==============================] - 2s 6ms/step - loss: 0.2162 - accuracy: 0.9534
Epoch 3/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1588 - accuracy: 0.9707
Epoch 4/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1389 - accuracy: 0.9769
Epoch 5/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1258 - accuracy: 0.9815
Epoch 6/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1162 - accuracy: 0.9846
Epoch 7/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1112 - accuracy: 0.9861
Epoch 8/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1067 - accuracy: 0.9880
Epoch 9/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0931 - accuracy: 0.9908
Epoch 10/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0935 - accuracy: 0.9911

Epoch 1/50
324/324 [==============================] - 2s 6ms/step - loss: 4.2413 - accuracy: 0.8015
Epoch 2/50
324/324 [==============================] - 2s 6ms/step - loss: 2.3699 - accuracy: 0.9486
Epoch 3/50
324/324 [==============================] - 2s 6ms/step - loss: 1.3303 - accuracy: 0.9586
Epoch 4/50
324/324 [==============================] - 2s 6ms/step - loss: 0.9132 - accuracy: 0.9632
Epoch 5/50
324/324 [==============================] - 2s 6ms/step - loss: 0.7473 - accuracy: 0.9626
Epoch 6/50
324/324 [==============================] - 2s 6ms/step - loss: 0.6475 - accuracy: 0.9673
Epoch 7/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5951 - accuracy: 0.9690
Epoch 8/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5840 - accuracy: 0.9672
Epoch 9/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5606 - accuracy: 0.9699
Epoch 10/50
324/324 [==============================] - 2s 6ms/step - loss: 0.5394 - accuracy: 0.9693

Epoch 1/50
324/324 [==============================] - 2s 6ms/step - loss: 54.4767 - accuracy: 0.7701
Epoch 2/50
324/324 [==============================] - 2s 6ms/step - loss: 3.0268 - accuracy: 0.8431
Epoch 3/50
324/324 [==============================] - 2s 6ms/step - loss: 2.9857 - accuracy: 0.8496
Epoch 4/50
324/324 [==============================] - 2s 6ms/step - loss: 2.9119 - accuracy: 0.8511
Epoch 5/50
324/324 [==============================] - 2s 6ms/step - loss: 2.8202 - accuracy: 0.8600
Epoch 6/50
324/324 [==============================] - 2s 6ms/step - loss: 2.7816 - accuracy: 0.8575
Epoch 7/50
324/324 [==============================] - 2s 6ms/step - loss: 2.7196 - accuracy: 0.8605
Epoch 8/50
324/324 [==============================] - 2s 6ms/step - loss: 2.6445 - accuracy: 0.8566
Epoch 9/50
324/324 [==============================] - 2s 6ms/step - loss: 2.6343 - accuracy: 0.8621
Epoch 10/50
324/324 [==============================] - 2s 6ms/step - loss: 2.6138 - accuracy: 0.856

Epoch 1/50
324/324 [==============================] - 2s 6ms/step - loss: 0.7058 - accuracy: 0.8024
Epoch 2/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1741 - accuracy: 0.9511
Epoch 3/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1164 - accuracy: 0.9701
Epoch 4/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0875 - accuracy: 0.9767
Epoch 5/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0760 - accuracy: 0.9812
Epoch 6/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0577 - accuracy: 0.9854
Epoch 7/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0557 - accuracy: 0.9863
Epoch 8/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0480 - accuracy: 0.9889
Epoch 9/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0401 - accuracy: 0.9907
Epoch 10/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0330 - accuracy: 0.9915

Epoch 1/50
324/324 [==============================] - 2s 6ms/step - loss: 0.6846 - accuracy: 0.8072
Epoch 2/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1872 - accuracy: 0.9506
Epoch 3/50
324/324 [==============================] - 2s 6ms/step - loss: 0.1196 - accuracy: 0.9680
Epoch 4/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0835 - accuracy: 0.9787
Epoch 5/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0706 - accuracy: 0.9809
Epoch 6/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0633 - accuracy: 0.9842
Epoch 7/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0493 - accuracy: 0.9871
Epoch 8/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0482 - accuracy: 0.9873
Epoch 9/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0382 - accuracy: 0.9901
Epoch 10/50
324/324 [==============================] - 2s 6ms/step - loss: 0.0346 - accuracy: 0.9907

In [17]:
# define the grid search parameters dropout
seed = 7
np.random.seed(seed)
errors = []
drops = []


dropouts = [0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]

for i in dropouts:
    model = Nakano_Net(i)
    error = evaluate(model, 56, 50, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
    errors.append(error)
    drops.append(i)

print("best error: %f" %(min(errors)))        

for error, d in zip(errors, drops):
    print("%f with: %f" % (error, d))
    
# best error 15.685755 with 0.4

TypeError: Nakano_Net() missing 1 required positional argument: 'l2'

In [66]:
# define the grid search parameters batch norm momentum
seed = 7
np.random.seed(seed)
errors = []
mom = []

momentum = [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]

for i in momentum:
    model = create_fnn(i)
    error = evaluate(model, 56, 200, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
    errors.append(error)
    mom.append(i)

print("best error: %f" %(min(errors)))        

for error, m in zip(errors, mom):
    print("%f with: %f" % (error, m))
    
# best 14.948958 with: 0.800000

Model: "model_422"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 1902)]            0         
_________________________________________________________________
dense_423 (Dense)            (None, 500)               951500    
_________________________________________________________________
dropout_423 (Dropout)        (None, 500)               0         
_________________________________________________________________
batch_normalization_422 (Bat (None, 500)               1500      
_________________________________________________________________
output_1 (Dense)             (None, 21)                10521     
Total params: 963,521
Trainable params: 962,521
Non-trainable params: 1,000
_________________________________________________________________
Epoch 1/200
324/324 [==============================] - 1s 2ms/step - loss: 0.6061 - accuracy: 0.9082
Epoch 2/200


324/324 [==============================] - 1s 2ms/step - loss: 0.0874 - accuracy: 0.9966
Epoch 151/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0960 - accuracy: 0.9954
Epoch 152/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0917 - accuracy: 0.9964
Epoch 153/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0909 - accuracy: 0.9963
Epoch 154/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0920 - accuracy: 0.9963
Epoch 155/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0889 - accuracy: 0.9965
Epoch 156/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0886 - accuracy: 0.9961
Epoch 157/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0910 - accuracy: 0.9961
Epoch 158/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0929 - accuracy: 0.9960
Epoch 159/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0981 - a

324/324 [==============================] - 1s 2ms/step - loss: 0.0960 - accuracy: 0.9959
Epoch 100/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0925 - accuracy: 0.9966
Epoch 101/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0967 - accuracy: 0.9959
Epoch 102/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0929 - accuracy: 0.9970
Epoch 103/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0950 - accuracy: 0.9956
Epoch 104/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0965 - accuracy: 0.9958
Epoch 105/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0892 - accuracy: 0.9963
Epoch 106/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0959 - accuracy: 0.9952
Epoch 107/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0967 - accuracy: 0.9960
Epoch 108/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0934 - a

324/324 [==============================] - 1s 2ms/step - loss: 0.1042 - accuracy: 0.9955
Epoch 49/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1017 - accuracy: 0.9961
Epoch 50/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1002 - accuracy: 0.9963
Epoch 51/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1012 - accuracy: 0.9960
Epoch 52/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0942 - accuracy: 0.9966
Epoch 53/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0970 - accuracy: 0.9956
Epoch 54/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0957 - accuracy: 0.9963
Epoch 55/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1018 - accuracy: 0.9957
Epoch 56/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0938 - accuracy: 0.9966
Epoch 57/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1022 - accuracy: 

324/324 [==============================] - 1s 2ms/step - loss: 0.5896 - accuracy: 0.9105
Epoch 2/200
324/324 [==============================] - 1s 2ms/step - loss: 0.2491 - accuracy: 0.9900
Epoch 3/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1806 - accuracy: 0.9955
Epoch 4/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1372 - accuracy: 0.9960
Epoch 5/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1195 - accuracy: 0.9963
Epoch 6/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1137 - accuracy: 0.9955
Epoch 7/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1101 - accuracy: 0.9954
Epoch 8/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1059 - accuracy: 0.9957
Epoch 9/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1055 - accuracy: 0.9956
Epoch 10/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1043 - accuracy: 0.9950
E

...

324/324 [==============================] - 1s 2ms/step - loss: 0.0889 - accuracy: 0.9960
Epoch 139/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0889 - accuracy: 0.9966
Epoch 140/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0928 - accuracy: 0.9956
Epoch 141/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0966 - accuracy: 0.9956
Epoch 142/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0948 - accuracy: 0.9959
Epoch 143/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0895 - accuracy: 0.9963
Epoch 144/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0876 - accuracy: 0.9964
Epoch 145/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0882 - accuracy: 0.9966
Epoch 146/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0903 - accuracy: 0.9964
Epoch 147/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0937 - a

324/324 [==============================] - 1s 2ms/step - loss: 0.0918 - accuracy: 0.9964
Epoch 88/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0929 - accuracy: 0.9960
Epoch 89/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0999 - accuracy: 0.9958
Epoch 90/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0989 - accuracy: 0.9956
Epoch 91/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0944 - accuracy: 0.9964
Epoch 92/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0906 - accuracy: 0.9967
Epoch 93/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0952 - accuracy: 0.9959
Epoch 94/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0973 - accuracy: 0.9957
Epoch 95/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0940 - accuracy: 0.9963
Epoch 96/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0952 - accuracy: 

324/324 [==============================] - 1s 2ms/step - loss: 0.1043 - accuracy: 0.9955
Epoch 36/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0976 - accuracy: 0.9961
Epoch 37/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0987 - accuracy: 0.9963
Epoch 38/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1001 - accuracy: 0.9956
Epoch 39/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1016 - accuracy: 0.9956
Epoch 40/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1042 - accuracy: 0.9955
Epoch 41/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0970 - accuracy: 0.9960
Epoch 42/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1018 - accuracy: 0.9950
Epoch 43/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1021 - accuracy: 0.9958
Epoch 44/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1012 - accuracy: 

324/324 [==============================] - 1s 2ms/step - loss: 0.0896 - accuracy: 0.9965
Epoch 195/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0933 - accuracy: 0.9961
Epoch 196/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0851 - accuracy: 0.9970
Epoch 197/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0891 - accuracy: 0.9962
Epoch 198/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0988 - accuracy: 0.9947
Epoch 199/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0969 - accuracy: 0.9958
Epoch 200/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0961 - accuracy: 0.9959
base error: 14.948958158493042
Model: "model_430"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 1902)]            0         
_____________________________________________

324/324 [==============================] - 1s 2ms/step - loss: 0.0967 - accuracy: 0.9962
Epoch 144/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0884 - accuracy: 0.9967
Epoch 145/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0889 - accuracy: 0.9963
Epoch 146/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0922 - accuracy: 0.9962
Epoch 147/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0948 - accuracy: 0.9960
Epoch 148/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0958 - accuracy: 0.9959
Epoch 149/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0990 - accuracy: 0.9964
Epoch 150/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0929 - accuracy: 0.9965
Epoch 151/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0920 - accuracy: 0.9962
Epoch 152/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0957 - a

In [21]:
# define the grid search parameters L1 L2
"""seed = 7
np.random.seed(seed)
errors = []
opts = []

optimizer = ['SGD', 'RMSprop', 'Adagrad', 'Adadelta', 'Adam', 'Adamax', 'Nadam']

for i in optimizer:
    model = Nakano_Net(i)
    error = evaluate(model, 56, 50, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
    errors.append(error)
    opts.append(i)"""

print("best error: %f" %(min(errors)))        

for error, m in zip(errors, opts):
    print("%f with: %s" % (error, m))
    
# best error 16.049713 with: Adam

best error: 17.319131
17.319131 with: SGD
17.461163 with: RMSprop
22.254771 with: Adagrad
59.236574 with: Adadelta
18.908125 with: Adam
18.872613 with: Adamax
19.067907 with: Nadam


In [39]:
# define the grid search parameters L1 L2
"""seed = 7
np.random.seed(seed)
errors = []
lr = []
b1 = []

lrs = [0.001, 0.002, 0.003, 0.004, 0.005, 0.0009, 0.0008, 0.0007, 0.0006, 0.0005]
mom = [0.1, 0.3, 0.5, 0.7, 0.9]

for i in lrs:
    for j in mom:
        model = Nakano_Net(i, j)
        error = evaluate(model, 56, 200, X_trainPCAScaler, one_hot_labels_train, X_validationPCAScaler, one_hot_labels_validation)
        errors.append(error)
        lr.append(i)
        b1.append(j)"""

print("best error: %f" %(min(errors)))        

for error, m, e in zip(errors, lr, b1):
    print("%f with: %f, %f" % (error, m, e))
    
# best error: 14.611632 with: 0.000800, 0.700000 and 0.900000
# best error: 16.058588 with: 0.005000, 0.900000

best error: 16.085219
20.266312 with: 0.001000, 0.100000
19.476253 with: 0.001000, 0.300000
18.002665 with: 0.001000, 0.500000
18.322235 with: 0.001000, 0.700000
17.168218 with: 0.001000, 0.900000
17.958277 with: 0.002000, 0.100000
19.076788 with: 0.002000, 0.300000
17.017311 with: 0.002000, 0.500000
17.718595 with: 0.002000, 0.700000
17.106080 with: 0.002000, 0.900000
17.851752 with: 0.003000, 0.100000
17.399025 with: 0.003000, 0.300000
16.884154 with: 0.003000, 0.500000
17.283624 with: 0.003000, 0.700000
16.493565 with: 0.003000, 0.900000
18.162447 with: 0.004000, 0.100000
17.949402 with: 0.004000, 0.300000
16.928542 with: 0.004000, 0.500000
16.857523 with: 0.004000, 0.700000
16.085219 with: 0.004000, 0.900000
17.691964 with: 0.005000, 0.100000


In [21]:
model = Nakano_Net()
model.fit(X_trainPCAScaler, one_hot_labels_train, epochs=200, batch_size=56, verbose=1) 
scores = model.evaluate(X_testPCAScaler, one_hot_labels_test, verbose=0)
error = 100-scores[1]*100
print("base error: "+str(error))

Epoch 1/200
324/324 [==============================] - 2s 5ms/step - loss: 1.7800 - accuracy: 0.4697
Epoch 2/200
324/324 [==============================] - 2s 6ms/step - loss: 1.0042 - accuracy: 0.6734
Epoch 3/200
324/324 [==============================] - 2s 6ms/step - loss: 0.7148 - accuracy: 0.7817
Epoch 4/200
324/324 [==============================] - 2s 5ms/step - loss: 0.5365 - accuracy: 0.8412
Epoch 5/200
324/324 [==============================] - 2s 5ms/step - loss: 0.4379 - accuracy: 0.8789
Epoch 6/200
324/324 [==============================] - 2s 5ms/step - loss: 0.3618 - accuracy: 0.9033
Epoch 7/200
324/324 [==============================] - 2s 5ms/step - loss: 0.3307 - accuracy: 0.9162
Epoch 8/200
324/324 [==============================] - 2s 5ms/step - loss: 0.2838 - accuracy: 0.9310
Epoch 9/200
324/324 [==============================] - 2s 5ms/step - loss: 0.2625 - accuracy: 0.9370
Epoch 10/200
324/324 [==============================] - 2s 5ms/step - loss: 0.2495 - accura

324/324 [==============================] - 2s 5ms/step - loss: 0.0688 - accuracy: 0.9921
Epoch 82/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0701 - accuracy: 0.9914
Epoch 83/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0631 - accuracy: 0.9937
Epoch 84/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0651 - accuracy: 0.9928
Epoch 85/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0657 - accuracy: 0.9928
Epoch 86/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0661 - accuracy: 0.9926
Epoch 87/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0631 - accuracy: 0.9935
Epoch 88/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0629 - accuracy: 0.9927
Epoch 89/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0650 - accuracy: 0.9927
Epoch 90/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0626 - accuracy: 

324/324 [==============================] - 2s 5ms/step - loss: 0.0510 - accuracy: 0.9966
Epoch 161/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0527 - accuracy: 0.9961
Epoch 162/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0512 - accuracy: 0.9964
Epoch 163/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0516 - accuracy: 0.9971
Epoch 164/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0509 - accuracy: 0.9965
Epoch 165/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0533 - accuracy: 0.9964
Epoch 166/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0502 - accuracy: 0.9969
Epoch 167/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0554 - accuracy: 0.9958
Epoch 168/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0498 - accuracy: 0.9966
Epoch 169/200
324/324 [==============================] - 2s 5ms/step - loss: 0.0554 - a

In [31]:
model = create_fnn()
model.fit(X_trainPCAScaler, one_hot_labels_train, epochs=200, batch_size=56, verbose=1) 
scores = model.evaluate(X_testPCAScaler, one_hot_labels_test, verbose=0)
error = 100-scores[1]*100
print("base error: "+str(error))

Epoch 1/200
324/324 [==============================] - 1s 2ms/step - loss: 0.6523 - accuracy: 0.8934
Epoch 2/200
324/324 [==============================] - 1s 2ms/step - loss: 0.2644 - accuracy: 0.9876
Epoch 3/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1942 - accuracy: 0.9943
Epoch 4/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1518 - accuracy: 0.9946
Epoch 5/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1308 - accuracy: 0.9956
Epoch 6/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1205 - accuracy: 0.9951
Epoch 7/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1187 - accuracy: 0.9949
Epoch 8/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1219 - accuracy: 0.9942
Epoch 9/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1169 - accuracy: 0.9943
Epoch 10/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1150 - accura

324/324 [==============================] - 1s 2ms/step - loss: 0.1044 - accuracy: 0.9948
Epoch 161/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1084 - accuracy: 0.9949
Epoch 162/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1082 - accuracy: 0.9952
Epoch 163/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1119 - accuracy: 0.9945
Epoch 164/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1009 - accuracy: 0.9964
Epoch 165/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1053 - accuracy: 0.9954
Epoch 166/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1063 - accuracy: 0.9949
Epoch 167/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1043 - accuracy: 0.9958
Epoch 168/200
324/324 [==============================] - 1s 2ms/step - loss: 0.0998 - accuracy: 0.9959
Epoch 169/200
324/324 [==============================] - 1s 2ms/step - loss: 0.1105 - a